In [1]:
import torch
from multiprocessing import set_start_method
from transformers import Blip2Processor, Blip2ForConditionalGeneration
from datasets import load_dataset

# Load BLIP-2 model and processor
processor = Blip2Processor.from_pretrained("Salesforce/blip2-opt-2.7b")
model = Blip2ForConditionalGeneration.from_pretrained("Salesforce/blip2-opt-2.7b", torch_dtype=torch.float16)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [11]:
def gpu_computation(batch, rank):
    device = f"cuda:{(rank or 0) % torch.cuda.device_count()}"
    model.to(device)
    inputs = processor(images=batch["image"], return_tensors="pt").to(device, torch.float16)

    with torch.no_grad():
        generated_ids = model.generate(**inputs, max_length=51)
    
    batch["caption"] = processor.batch_decode(generated_ids, skip_special_tokens=True)
    return batch

In [12]:
import multiprocessing


if __name__ == "__main__":
    # Check if start method is already set
    try:
        multiprocessing.get_start_method()
    except RuntimeError:
        multiprocessing.set_start_method("spawn")

    # Load your dataset
    dataset = load_dataset("visual-layer/oxford-iiit-pet-vl-enriched", split="train")
    dataset = dataset.select(range(10))

    updated_dataset = dataset.map(
        gpu_computation,
        batched=True,
        batch_size=4,  # Adjust based on your GPU memory
        with_rank=True,
        num_proc=torch.cuda.device_count(),  # one process per GPU
    )

Map:   0%|          | 0/10 [00:00<?, ? examples/s]

In [13]:
updated_dataset['caption']

['a cat walking on grass\n',
 'a white dog playing with a ball\n',
 'a dog sitting in the grass\n',
 'a dog laying in the grass\n',
 'a dog standing in the snow\n',
 'a dog laying in the grass\n',
 'a dog laying on a brick sidewalk\n',
 'a man holding a black dog\n',
 'a large dog standing in the grass\n',
 'a pug dog with its tongue out standing on a tiled floor\n']